In [ ]:
# Avoids scroll-in-the-scroll in the entire Notebook
from IPython.display import Javascript
def resize_colab_cell():
  display(Javascript('google.colab.output.setIframeHeight(0, true, {maxHeight: 300})'))
get_ipython().events.register('pre_run_cell', resize_colab_cell)

<IPython.core.display.Javascript object>

#Yummly28K Parser
Yummly28K is a large recipe/food dataset widely used among academic sources. The diet optimizing engine uses this recipe data for creating meal plans. This notebook parses the raw dataset and returns a json file with the used information.

*Shaun Maher*

## Download and unpack the archive from source 

In [ ]:
import json
import pandas as pd
import glob

!wget http://lherranz.org/local/datasets/yummly28k/Yummly28K.rar && unrar x "Yummly28K.rar" "Yummly28K/"

<IPython.core.display.Javascript object>

Streaming output truncated to the last 5000 lines.
Extracting  Yummly28K/metadata27638/meta22640.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22641.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22642.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22643.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22644.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22645.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22646.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22647.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22648.json                        98%  OK 
Extracting  Yummly28K/metadata27638/meta22649.json                        98%  OK 
Extracting  Yummly28K/metadat

## Build recipe index

In [ ]:
recipes = []
for file in glob.glob("Yummly28K/metadata27638/*.json"):
    recipes.append(file)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Parse each file into master object

In [ ]:
total_recipes = len(recipes)

parsed = {}
for i, recipe in enumerate(recipes):
  print("Proccessing {} ({} of {} - {}%)".format(recipe, i + 1, total_recipes, round((i/total_recipes) * 100, 2)))
  recipe_number = int(recipe.split("meta")[-1][:-5]) # We want to preserve the original file id
  with open(recipe) as f:
      data = json.load(f)
      calories = 0
      fat = 0
      carbohydrates = 0
      protein = 0 
      sugar = 0 
      sodium = 0 

      # No good way to extract the macros, we will go through the recipe attributes and pull them
      for entry in data["nutritionEstimates"]:
        if entry["attribute"] == "ENERC_KCAL":
          calories = entry["value"]
        elif entry["attribute"] == "FAT":
          fat = entry["value"]
        elif entry["attribute"] == "CHOCDF":
          carbohydrates = entry["value"]
        elif entry["attribute"] == "PROCNT":
          protein = entry["value"]
        elif entry["attribute"] == "SUGAR":
          sugar = entry["value"]      
        elif entry["attribute"] == "NA":
          sodium = entry["value"]

      # The format used by optimizer
      recipe_obj = {
          "id": recipe_number,
          "name": data["name"],
          "ingredients": data["ingredientLines"],
          "rating": data["rating"],
          "seconds": data["totalTimeInSeconds"],
          "src": data["source"].get('sourceRecipeUrl', None) if data["source"].get('sourceRecipeUrl', None) else data["attribution"].get('url', None),
          "course": data["attributes"]["course"], # this was originally named "type" but I am changing it because that sometimes causes problems depending on the lang
          "cuisine": data["attributes"]["cuisine"],
          "calories": round(calories),
          "carbohydrates": round(carbohydrates),
          "fat": round(fat),
          "protein": round(protein),
          "sugar": round(sugar),
          "sodium": round(sodium,2),
          "quantity": 1
      }
      if calories == fat == carbohydrates == protein == 0:
        print("Missing key nutrients, skipping")
      else:
        parsed[recipe_number] = recipe_obj

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Streaming output truncated to the last 5000 lines.
Proccessing Yummly28K/metadata27638/meta03082.json (23061 of 27638 - 83.44%)
Proccessing Yummly28K/metadata27638/meta06345.json (23062 of 27638 - 83.44%)
Missing key nutrients, skipping
Proccessing Yummly28K/metadata27638/meta26450.json (23063 of 27638 - 83.45%)
Proccessing Yummly28K/metadata27638/meta26940.json (23064 of 27638 - 83.45%)
Proccessing Yummly28K/metadata27638/meta05896.json (23065 of 27638 - 83.45%)
Proccessing Yummly28K/metadata27638/meta06739.json (23066 of 27638 - 83.46%)
Proccessing Yummly28K/metadata27638/meta18101.json (23067 of 27638 - 83.46%)
Proccessing Yummly28K/metadata27638/meta19946.json (23068 of 27638 - 83.46%)
Proccessing Yummly28K/metadata27638/meta25774.json (23069 of 27638 - 83.47%)
Proccessing Yummly28K/metadata27638/meta07624.json (23070 of 27638 - 83.47%)
Missing key nutrients, skipping
Proccessing Yummly28K/metadata27638/meta22999.json (23071 of 27638 - 83.48%)
Proccessing Yummly28K/metadata27638/me

## Load parsed recipes into DataFrame for filtering 
(add any additional processing here)

In [ ]:
df = pd.DataFrame.from_dict(parsed, orient='index').sort_values("id")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

We want to remove drinks and condiments from our recipe selection because people likely do not want those as a meal

In [ ]:
selection = ['Cocktails', 'Condiments and Sauces']

mask = df["course"].apply(lambda x: any(item for item in selection if item in x))
df = df[~mask].reset_index(drop=True)

print("Our selection will include: {}".format(df["course"].explode().unique()))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Our selection will include: ['Side Dishes' 'Main Dishes' 'Desserts' 'Salads' 'Soups' 'Appetizers'
 'Breads' 'Lunch and Snacks' 'Breakfast and Brunch' 'Beverages'
 'Afternoon Tea']


In [ ]:
# Sanity Check - Random Sample of 30 

df.sample(frac=1).head(30)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

id                                               name  \
7445    8589    Hamburger Steak With Sweet Onion-Mushroom Gravy   
2328    2678                           Bucatini All'amatriciana   
789      924                Buffalo Chicken Enchilada Casserole   
8392    9665                                 Pecan Pastry Shell   
19349  22250                            Grilled Beef Tenderloin   
13488  15486                         Penne & Sausage Casseroles   
20736  23844                                 Chocolate Silk Pie   
16909  19428                            Chicken Tortilla Soup I   
16371  18821           Baby Artichokes with Olives en Papillote   
14418  16558              Miesmuscheln in Curry - Weißweinsahne   
19178  22056  Fridge Crisper Salad with Grilled Cheese Croutons   
9726   11188                                      Salmon Mousse   
10136  11653                             Ground Turkey and Tofu   
18214  20943           Texas Dry-Rub Slow-Grilled Turkey Breast   
10171  11697                                Curried Cauliflower   
6186    7137                              Chicken Tortilla Soup   
7162    8274                      Texas Pecan and Chocolate Pie   
3742    4297          Roast Chicken and Mango Salad with Yogurt   
22365  25719                                      Falsche Pizza   
9475   10893                                Onion Soup Gratinee   
14551  16718                                  FRENCH ONION SOUP   
85        99        Italian Garbanzo Bean Sun Dried Tomato Soup   
1655    1911          Cheese-Stuffed Poblanos with Tomato Sauce   
8270    9530          Balsamic-Rosemary Roasted Root Vegetables   
20661  23760                                      Arugula Pesto   
4822    5556                       Chipotle Chicken Quesadillas   
20256  23296                                    Vermont Burgers   
20268  23311                           Oven-Roasted Green Beans   
12688  14576                    Italian Sausage Stuffed Peppers   
21077  24235                             Super Simple Guacamole   

                                             ingredients  rating  seconds  \
7445   [2 honey-wheat bread slices, 1 pound ground ro...       3   2100.0   
2328   [3 tablespoons extra-virgin olive oil, divided...       4   2100.0   
789    [1 pound cooked chicken breast, shredded, 1 me...       3   2700.0   
8392   [1/2 cup pecan pieces, 1 1/4 cups all-purpose ...       4   5400.0   
19349  [1 beef tenderloin (4 pounds), preferably gras...       4   6000.0   
13488  [1-1/2 pounds uncooked penne pasta, 1 pound Jo...       3   4800.0   
20736  [7 ounces chocolate sandwich cookies (about 17...       4      NaN   
16909  [1 onion, chopped, 3 cloves garlic, minced, 1 ...       5   2400.0   
16371  [8 teaspoons fresh lemon juice, plus 1/2 lemon...       3   3300.0   
14418  [2 kg Muschel(n) (Miesmuscheln), 2 Zwiebel(n),...       3   1200.0   
19178  [1/4 of a medium-sized juicy lime, juiced, 1 d...       0    900.0   
9726   [8 oz. smoked salmon, flaked with a fork, 8 oz...       0   3300.0   
10136  [1 (14-ounce) package water-packed firm reduce...       4   2700.0   
18214  [1 cup hickory wood chips, 1 tablespoon Hungar...       4      NaN   
10171  [2 teaspoons olive oil, 2 cups thinly sliced o...       4   2400.0   
6186   [Canola oil for frying, 5 corn tortillas, cut ...       4   3300.0   
7162   [1 cup all purpose flour, 6 tablespoons (3/4 s...       5   4800.0   
3742   [3 tablespoons extra-virgin olive oil, 2 table...       5   1500.0   
22365  [250 g Tomaten, 1 kleine Zwiebel, 1 EL Olivenö...       3   2700.0   
9475   [6 tablespoons olive oil, 4 medium yellow onio...       5   8100.0   
14551  [3 tablespoons unsalted butter, cut into 3 pie...       4      NaN   
85     [1 cup small pasta shells, 1 1/2 Tbsp. olive o...       4   2400.0   
1655   [4 large fresh poblano chiles (1 pound), 1/2 p...       5   5400.0   
8270   [2 tablespoons extra-virgin olive oil, 1 table...       4   2700.0   
20661  

## Export the data to a json file on Colab
Find this file on the left pane

In [ ]:
json_str = df.to_json(orient="index")
parsed_json = json.loads(json_str)
with open("foods.json", 'w') as json_file:
    json_file.write(json.dumps(parsed_json))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>